In [1]:
import fiona

# Paths to your .gdb directories
gdb_paths = [
    "USA_Boundaries_2023.gdb",
    "Transportation_v1.gdb",
    "buffered%20layer.gdb"
]

# List layers in each geodatabase
layer_names = {} #Used to store the layers from each gdb
for gdb in gdb_paths:
    print(f"Layers in {gdb}:")
    print(fiona.listlayers(gdb))
    layer_names[gdb] = fiona.listlayers(gdb)



Layers in USA_Boundaries_2023.gdb:
['USA_ZipCode']
Layers in Transportation_v1.gdb:
['Primary_Roads_Interstates_5M_scale', 'Primary_Roads_2_1M_scale', 'Primary_Roads', 'Secondary_Roads_Interstates_and_US_Highways', 'Secondary_Roads_578k_scale', 'Secondary_Roads_289_144k_scale', 'Secondary_Roads_72_1k_scale']
Layers in buffered%20layer.gdb:
['BufferedFeatures']


In [2]:
import geopandas as gpd

# Path to your .gdb directory
gdb_path = "USA_Boundaries_2023.gdb"

# Load the boundaries into a GeoDataFrame using GeoPandas
boundaries = gpd.read_file(gdb_path, layer='USA_ZipCode')

# Print unique zip codes from the boundaries layer
if 'ZIP_CODE' in boundaries.columns:  # Adjust this column name if necessary
    unique_zip_codes = boundaries['ZIP_CODE'].unique()
    print("Unique zip codes in USA_Boundaries_2023.gdb:")
    for zip_code in unique_zip_codes:
        print(zip_code)
else:
    print("Column 'ZIP_CODE' not found in the boundaries layer.")


Unique zip codes in USA_Boundaries_2023.gdb:
20007


In [3]:
import geopandas as gpd
import requests
import folium
from shapely.geometry import LineString, MultiLineString

# Load the buffered layer
buffered_layer_name = layer_names["buffered%20layer.gdb"][0]  
buffered_layer = gpd.read_file(gdb_paths[2], layer=buffered_layer_name)

# Get bounding box of buffered region
minx, miny, maxx, maxy = buffered_layer.total_bounds
bbox_str = f"{miny},{minx},{maxy},{maxx}"  # Overpass uses (S,W,N,E)

# Query Overpass API for driveable roads only
overpass_url = "http://overpass-api.de/api/interpreter"
query = f"""
[out:json];
(
  way["highway"~"motorway|trunk|primary|secondary|tertiary|unclassified|residential|service"]({bbox_str});
);
out geom;
"""
response = requests.get(overpass_url, params={'data': query})
data = response.json()

# Convert Overpass API response to GeoDataFrame
road_features = []
for element in data["elements"]:
    if "geometry" in element:
        line_coords = [(pt["lon"], pt["lat"]) for pt in element["geometry"]]
        road_features.append(LineString(line_coords))

# Create GeoDataFrame
roads_gdf = gpd.GeoDataFrame(geometry=road_features, crs="EPSG:4326")

# Clip roads to the buffered region
roads_clipped = roads_gdf.clip(buffered_layer)

# Get the centroid of the buffered region for map centering
centroid = buffered_layer.geometry.centroid.iloc[0]
m = folium.Map(location=[centroid.y, centroid.x], zoom_start=14)

# Function to extract coordinates from LineString and MultiLineString
def extract_coords(geometry):
    if isinstance(geometry, LineString):
        return [(point[1], point[0]) for point in geometry.coords]  # Convert (x, y) to (lat, lon)
    elif isinstance(geometry, MultiLineString):
        return [[(point[1], point[0]) for point in line.coords] for line in geometry.geoms]  # Convert for each line
    return []

# Add clipped road segments to the map
for _, row in roads_clipped.iterrows():
    coords = extract_coords(row.geometry)
    if isinstance(coords[0], list):  # If MultiLineString, plot each sub-line separately
        for sub_coords in coords:
            folium.PolyLine(sub_coords, color="blue", weight=2).add_to(m)
    else:  # If LineString, plot normally
        folium.PolyLine(coords, color="blue", weight=2).add_to(m)

# Display the map
m


C:\Users\theod\AppData\Local\Temp\ipykernel_26024\3577450000.py:40: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = buffered_layer.geometry.centroid.iloc[0]


In [4]:
import geopandas as gpd
import requests
import folium
from shapely.geometry import LineString, MultiLineString

# Load the boundaries layer
boundaries_layer_name = layer_names["USA_Boundaries_2023.gdb"][0]
boundaries = gpd.read_file(gdb_paths[0], layer=boundaries_layer_name)

# Get bounding box of boundaries layer
minx, miny, maxx, maxy = boundaries.total_bounds
bbox_str = f"{miny},{minx},{maxy},{maxx}"  # Overpass uses (S,W,N,E)

# Query Overpass API for driveable roads only within the boundaries
overpass_url = "http://overpass-api.de/api/interpreter"
query = f"""
[out:json];
(
  way["highway"~"motorway|trunk|primary|secondary|tertiary|unclassified|residential|service"]({bbox_str});
);
out geom;
"""
response = requests.get(overpass_url, params={'data': query})
data = response.json()

# Convert Overpass API response to GeoDataFrame
road_features = []
for element in data["elements"]:
    if "geometry" in element:
        line_coords = [(pt["lon"], pt["lat"]) for pt in element["geometry"]]
        road_features.append(LineString(line_coords))

# Create GeoDataFrame for roads
roads_gdf = gpd.GeoDataFrame(geometry=road_features, crs="EPSG:4326")

# Clip roads to the boundaries region
roads_clipped = roads_gdf.clip(boundaries)

# Get the centroid of the boundaries region for map centering
centroid = boundaries.geometry.centroid.iloc[0]
m = folium.Map(location=[centroid.y, centroid.x], zoom_start=14)

# Function to extract coordinates from LineString and MultiLineString
def extract_coords(geometry):
    if isinstance(geometry, LineString):
        return [(point[1], point[0]) for point in geometry.coords]  # Convert (x, y) to (lat, lon)
    elif isinstance(geometry, MultiLineString):
        return [[(point[1], point[0]) for point in line.coords] for line in geometry.geoms]  # Convert for each line
    return []

# Add clipped road segments to the map
for _, row in roads_clipped.iterrows():
    coords = extract_coords(row.geometry)
    if isinstance(coords[0], list):  # If MultiLineString, plot each sub-line separately
        for sub_coords in coords:
            folium.PolyLine(sub_coords, color="blue", weight=2).add_to(m)
    else:  # If LineString, plot normally
        folium.PolyLine(coords, color="blue", weight=2).add_to(m)

# Display the map
m


C:\Users\theod\AppData\Local\Temp\ipykernel_26024\1379168941.py:40: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = boundaries.geometry.centroid.iloc[0]


In [5]:
import geopandas as gpd
import requests
import folium
from shapely.geometry import LineString, MultiLineString

# Load the buffered layer
buffered_layer_name = layer_names["buffered%20layer.gdb"][0]  
buffered_layer = gpd.read_file(gdb_paths[2], layer=buffered_layer_name)

# Load the boundaries layer
boundaries_layer_name = layer_names["USA_Boundaries_2023.gdb"][0]
boundaries = gpd.read_file(gdb_paths[0], layer=boundaries_layer_name)

# Get bounding box of boundaries layer
minx, miny, maxx, maxy = boundaries.total_bounds
bbox_str = f"{miny},{minx},{maxy},{maxx}"  # Overpass uses (S,W,N,E)

# Query Overpass API for driveable roads only
overpass_url = "http://overpass-api.de/api/interpreter"
query = f"""
[out:json];
(
  way["highway"~"motorway|trunk|primary|secondary|tertiary|unclassified|residential|service"]({bbox_str});
);
out geom;
"""
response = requests.get(overpass_url, params={'data': query})
data = response.json()

# Convert Overpass API response to GeoDataFrame
road_features = []
for element in data["elements"]:
    if "geometry" in element:
        line_coords = [(pt["lon"], pt["lat"]) for pt in element["geometry"]]
        road_features.append(LineString(line_coords))

# Create GeoDataFrame for roads
roads_gdf = gpd.GeoDataFrame(geometry=road_features, crs="EPSG:4326")

# Clip roads to the boundaries region
roads_within_boundaries = roads_gdf.clip(boundaries)

# Find roads outside of boundaries but within the buffered layer
roads_outside_boundaries = roads_gdf[~roads_gdf.geometry.within(boundaries.geometry.unary_union)]
roads_outside_boundaries = roads_outside_boundaries.clip(buffered_layer)

# Get the centroid of the boundaries region for map centering
centroid = boundaries.geometry.centroid.iloc[0]
m = folium.Map(location=[centroid.y, centroid.x], zoom_start=14)

# Function to extract coordinates from LineString and MultiLineString
def extract_coords(geometry):
    if isinstance(geometry, LineString):
        return [(point[1], point[0]) for point in geometry.coords]  # Convert (x, y) to (lat, lon)
    elif isinstance(geometry, MultiLineString):
        return [[(point[1], point[0]) for point in line.coords] for line in geometry.geoms]  # Convert for each line
    return []

# Add roads within boundaries to the map in blue
for _, row in roads_within_boundaries.iterrows():
    coords = extract_coords(row.geometry)
    folium.PolyLine(coords, color="blue", weight=2).add_to(m)

# Add roads outside boundaries but within buffered layer to the map in black
for _, row in roads_outside_boundaries.iterrows():
    coords = extract_coords(row.geometry)
    folium.PolyLine(coords, color="black", weight=2).add_to(m)

# Display the map
m


C:\Users\theod\AppData\Local\Temp\ipykernel_26024\3363352129.py:44: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  roads_outside_boundaries = roads_gdf[~roads_gdf.geometry.within(boundaries.geometry.unary_union)]
C:\Users\theod\AppData\Local\Temp\ipykernel_26024\3363352129.py:48: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = boundaries.geometry.centroid.iloc[0]


In [6]:
import geopandas as gpd
import requests
import folium
from shapely.geometry import LineString, MultiLineString, Point, GeometryCollection
from shapely.ops import split

# Load the buffered layer
buffered_layer_name = layer_names["buffered%20layer.gdb"][0]  
buffered_layer = gpd.read_file(gdb_paths[2], layer=buffered_layer_name)

# Load the boundaries layer
boundaries_layer_name = layer_names["USA_Boundaries_2023.gdb"][0]
boundaries = gpd.read_file(gdb_paths[0], layer=boundaries_layer_name)

# Get bounding box of boundaries layer
minx, miny, maxx, maxy = boundaries.total_bounds
bbox_str = f"{miny},{minx},{maxy},{maxx}"  # Overpass uses (S,W,N,E)

# Query Overpass API for driveable roads only so we don't get sidewalks
overpass_url = "http://overpass-api.de/api/interpreter"
query = f"""
[out:json];
(
  way["highway"~"motorway|trunk|primary|secondary|tertiary|unclassified|residential|service"]({bbox_str});
);
out geom;
"""
response = requests.get(overpass_url, params={'data': query})
data = response.json()

# Convert Overpass API response to GeoDataFrame
road_features = []
for element in data["elements"]:
    if "geometry" in element:
        line_coords = [(pt["lon"], pt["lat"]) for pt in element["geometry"]]
        road_features.append(LineString(line_coords))

# Create GeoDataFrame for roads
roads_gdf = gpd.GeoDataFrame(geometry=road_features, crs="EPSG:4326")

# Clip roads to the boundaries region
roads_within_boundaries = roads_gdf.clip(boundaries)

# Find road intersections
def find_intersections(roads):
    """Finds intersection points of road segments."""
    intersections = []
    for i, road1 in roads.iterrows():
        for j, road2 in roads.iterrows():
            if i >= j:
                continue  # Avoid self-comparison and duplicates
            inter = road1.geometry.intersection(road2.geometry)
            if inter.is_empty:
                continue
            # Handle both Point and GeometryCollection cases
            if isinstance(inter, Point):
                intersections.append(inter)
            elif isinstance(inter, GeometryCollection):
                for geom in inter.geoms:
                    if isinstance(geom, Point):
                        intersections.append(geom)
    return intersections

# Get intersection points
intersection_points = find_intersections(roads_within_boundaries)

# Create a GeoDataFrame for intersection points
intersections_gdf = gpd.GeoDataFrame(geometry=intersection_points, crs="EPSG:4326")

# Split roads into segments at intersections
def split_road_segments(road, intersection_points):
    """Splits a road into segments at given intersection points."""
    segments = [road]
    for point in intersection_points:
        new_segments = []
        for segment in segments:
            if segment.intersects(point):
                split_segments = split(segment, point)
                if isinstance(split_segments, GeometryCollection):
                    # Extract individual geometries from GeometryCollection
                    new_segments.extend([geom for geom in split_segments.geoms])
                else:
                    new_segments.append(split_segments)
            else:
                new_segments.append(segment)
        segments = new_segments
    return segments

# Create segments for each road
road_segments = []
for _, road in roads_within_boundaries.iterrows():
    segments = split_road_segments(road.geometry, intersection_points)
    road_segments.extend(segments)

# Create GeoDataFrame for road segments
road_segments_gdf = gpd.GeoDataFrame(geometry=road_segments, crs="EPSG:4326")

# Get the centroid of the boundaries region for map centering
centroid = boundaries.geometry.centroid.iloc[0]
m = folium.Map(location=[centroid.y, centroid.x], zoom_start=14)

def extract_coords(geometry):
    if isinstance(geometry, LineString):
        return [(point[1], point[0]) for point in geometry.coords]  # Convert (x, y) to (lat, lon)
    elif isinstance(geometry, MultiLineString):
        return [[(point[1], point[0]) for point in line.coords] for line in geometry.geoms]  # Convert for each line
    return []

# Add road segments to the map in blue
for _, row in road_segments_gdf.iterrows():
    coords = extract_coords(row.geometry)
    folium.PolyLine(coords, color="blue", weight=2).add_to(m)

# Add roads outside boundaries but within buffered layer to the map in black
for _, row in roads_gdf.clip(buffered_layer).iterrows():
    coords = extract_coords(row.geometry)
    folium.PolyLine(coords, color="black", weight=2).add_to(m)

# Display the map
m


C:\Users\theod\AppData\Local\Temp\ipykernel_26024\3178394499.py:99: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = boundaries.geometry.centroid.iloc[0]


In [7]:
import geopandas as gpd
import requests
import folium
from shapely.geometry import LineString, MultiLineString
import geohash2
import random

# Function to generate a random color
def get_random_color():
    return f'#{random.randint(0, 0xFFFFFF):06x}'  # Generate a random hex color

# Function to extract coordinates from LineString and MultiLineString
def extract_coords(geometry):
    if isinstance(geometry, LineString):
        return [(point[1], point[0]) for point in geometry.coords]  # Convert (x, y) to (lat, lon)
    elif isinstance(geometry, MultiLineString):
        return [[(point[1], point[0]) for point in line.coords] for line in geometry.geoms]  # Convert for each line
    return []

# Initialize a list to store GeoHashes and a dictionary to track assigned GeoHashes
geohash_list = []
geohash_dict = {}  # Dictionary to track unique GeoHashes

# Create a new map centered on the same location
m = folium.Map(location=[centroid.y, centroid.x], zoom_start=14)

# Loop through the road segments and plot them with different colors
for road in roads_clipped.geometry:
    # Split the road into segments at intersection points
    
    intersection_points = [] 
    segments = split_road_segments(road, intersection_points)
    
    for segment in segments:
        coords = extract_coords(segment)
        color = get_random_color()  # Get a random color for each segment

        # Determine the start and end points for unique identification
        if isinstance(segment, LineString):
            start_point = (segment.coords[0][0], segment.coords[0][1])  # (lon, lat)
            end_point = (segment.coords[-1][0], segment.coords[-1][1])  # (lon, lat)
        elif isinstance(segment, MultiLineString):
            # Use the coordinates of the first line segment as representative points
            start_point = (segment.geoms[0].coords[0][0], segment.geoms[0].coords[0][1])  # (lon, lat)
            end_point = (segment.geoms[0].coords[-1][0], segment.geoms[0].coords[-1][1])  # (lon, lat)

        unique_id = f"{start_point}-{end_point}"

        # Generate a GeoHash for the segment if it hasn't been assigned
        if unique_id not in geohash_dict:
            centroid = segment.centroid
            geohash = geohash2.encode(centroid.y, centroid.x, precision=7)  # Adjust precision as needed
            geohash_dict[unique_id] = geohash  # Store the GeoHash with the unique identifier

        # Retrieve the GeoHash from the dictionary
        geohash = geohash_dict[unique_id]
        geohash_list.append(geohash)

        # Plot the segment on the map
        folium.PolyLine(coords, color=color, weight=2).add_to(m)

# Display the map with colored segments
m

# Optionally, print the list of unique GeoHashes
#print("List of Unique GeoHashes:", geohash_list)
